In [1]:
print("Hello, World!!")

Hello, World!!


In [2]:
import os
# Set working directory to project root so relative paths resolve consistently
os.chdir(r"D:\Sai Teja Honours\GenmedAssist")
print('CWD set to', os.getcwd())

CWD set to D:\Sai Teja Honours\GenmedAssist


In [3]:
%pwd

'D:\\Sai Teja Honours\\GenmedAssist'

In [4]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

c:\Users\Faculty\anaconda3\envs\GenmedAssist\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [5]:
from pathlib import Path
from langchain_community.document_loaders import PyPDFLoader

def load_pdf_files(data):
    pdf_files = Path(data).glob("*.pdf")
    documents = []
    for pdf in pdf_files:
        loader = PyPDFLoader(str(pdf))
        documents.extend(loader.load())
    return documents

In [6]:
extracted_data = load_pdf_files("data")

In [7]:
len(extracted_data)

637

In [8]:
from typing import List
from langchain.schema import Document

def filter_to_minimal_docs(documents: List[Document]) -> List[Document]:
    """
    Given a list of Document objects, return a new list of Document objects
    containing only the original page_content and a metadata dict with 'source'.
    """
    minimal_docs: List[Document] = []
    for doc in documents:
        src = doc.metadata.get("source") if isinstance(doc.metadata, dict) else None
        minimal_docs.append(Document(page_content=doc.page_content, metadata={"source": src}))
    return minimal_docs

In [9]:
minimal_docs = filter_to_minimal_docs(extracted_data)

In [10]:
minimal_docs

[Document(metadata={'source': 'data\\Medical_book.pdf'}, page_content=''),
 Document(metadata={'source': 'data\\Medical_book.pdf'}, page_content='The GALE\nENCYCLOPEDIA\nof MEDICINE\nSECOND EDITION'),
 Document(metadata={'source': 'data\\Medical_book.pdf'}, page_content='The GALE\nENCYCLOPEDIA\nof MEDICINE\nSECOND EDITION\nJACQUELINE L. LONGE, EDITOR\nDEIRDRE S. BLANCHFIELD, ASSOCIATE EDITOR\nVOLUME\nA-B\n1'),
 Document(metadata={'source': 'data\\Medical_book.pdf'}, page_content='STAFF\nJacqueline L. Longe, Project Editor\nDeirdre S. Blanchfield, Associate Editor\nChristine B. Jeryan, Managing Editor\nDonna Olendorf, Senior Editor\nStacey Blachford, Associate Editor\nKate Kretschmann, Melissa C. McDade, Ryan\nThomason, Assistant Editors\nMark Springer, Technical Specialist\nAndrea Lopeman, Programmer/Analyst\nBarbara J. Yarrow,Manager, Imaging and Multimedia\nContent\nRobyn V . Young,Project Manager, Imaging and\nMultimedia Content\nDean Dauphinais, Senior Editor, Imaging and\nMultimed

In [11]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
import re

# --- Clean Function ---
def clean_text(text):
    """Remove unwanted characters and normalize spacing."""
    text = text.replace('\n', ' ')               # Replace newlines with spaces
    text = re.sub(r'\s+', ' ', text).strip()     # Remove multiple spaces
    return text

# --- Split + Clean Function ---
def text_split(minimal_docs):
    """Clean and split documents into smaller chunks."""
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=500,
        chunk_overlap=20,
    )

    cleaned_docs = []
    for doc in minimal_docs:
        doc.page_content = clean_text(doc.page_content)
        cleaned_docs.append(doc)

    # Split the cleaned docs
    texts_chunk = text_splitter.split_documents(cleaned_docs)

    # Clean each chunk again (safety pass)
    for chunk in texts_chunk:
        chunk.page_content = clean_text(chunk.page_content)

    # Print all cleaned chunks before embedding
    print("\n📄 --- Cleaned Text Chunks ---\n")
    for i, chunk in enumerate(texts_chunk, 1):
        print(f"Chunk {i}:")
        print(chunk.page_content)
        print("-" * 80)

    return texts_chunk

In [12]:
texts_chunk = text_split(minimal_docs)


📄 --- Cleaned Text Chunks ---

Chunk 1:
The GALE ENCYCLOPEDIA of MEDICINE SECOND EDITION
--------------------------------------------------------------------------------
Chunk 2:
The GALE ENCYCLOPEDIA of MEDICINE SECOND EDITION JACQUELINE L. LONGE, EDITOR DEIRDRE S. BLANCHFIELD, ASSOCIATE EDITOR VOLUME A-B 1
--------------------------------------------------------------------------------
Chunk 3:
STAFF Jacqueline L. Longe, Project Editor Deirdre S. Blanchfield, Associate Editor Christine B. Jeryan, Managing Editor Donna Olendorf, Senior Editor Stacey Blachford, Associate Editor Kate Kretschmann, Melissa C. McDade, Ryan Thomason, Assistant Editors Mark Springer, Technical Specialist Andrea Lopeman, Programmer/Analyst Barbara J. Yarrow,Manager, Imaging and Multimedia Content Robyn V . Young,Project Manager, Imaging and Multimedia Content Dean Dauphinais, Senior Editor, Imaging and
--------------------------------------------------------------------------------
Chunk 4:
Editor, Imaging a

In [13]:
texts_chunk = text_split(minimal_docs)
print(f"Number of chunks: {len(texts_chunk)}")


📄 --- Cleaned Text Chunks ---

Chunk 1:
The GALE ENCYCLOPEDIA of MEDICINE SECOND EDITION
--------------------------------------------------------------------------------
Chunk 2:
The GALE ENCYCLOPEDIA of MEDICINE SECOND EDITION JACQUELINE L. LONGE, EDITOR DEIRDRE S. BLANCHFIELD, ASSOCIATE EDITOR VOLUME A-B 1
--------------------------------------------------------------------------------
Chunk 3:
STAFF Jacqueline L. Longe, Project Editor Deirdre S. Blanchfield, Associate Editor Christine B. Jeryan, Managing Editor Donna Olendorf, Senior Editor Stacey Blachford, Associate Editor Kate Kretschmann, Melissa C. McDade, Ryan Thomason, Assistant Editors Mark Springer, Technical Specialist Andrea Lopeman, Programmer/Analyst Barbara J. Yarrow,Manager, Imaging and Multimedia Content Robyn V . Young,Project Manager, Imaging and Multimedia Content Dean Dauphinais, Senior Editor, Imaging and
--------------------------------------------------------------------------------
Chunk 4:
Editor, Imaging a

In [14]:
from langchain.embeddings import HuggingFaceEmbeddings

def download_embeddings():
    """
    Download and return the HuggingFace embeddings model.
    """
    model_name = "sentence-transformers/all-MiniLM-L6-v2"
    embeddings = HuggingFaceEmbeddings(
        model_name=model_name
    )
    return embeddings

embedding = download_embeddings()

C:\Users\Faculty\AppData\Local\Temp\ipykernel_15952\30168171.py:8: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceEmbeddings(


In [15]:
embedding

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False, 'architecture': 'BertModel'})
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
), model_name='sentence-transformers/all-MiniLM-L6-v2', cache_folder=None, model_kwargs={}, encode_kwargs={}, multi_process=False, show_progress=False)

In [16]:
vector = embedding.embed_query("Hello world")
vector

[-0.03447727486491203,
 0.03102312609553337,
 0.006734980270266533,
 0.026108933612704277,
 -0.03936205804347992,
 -0.16030246019363403,
 0.06692394614219666,
 -0.006441438104957342,
 -0.047450482845306396,
 0.014758863486349583,
 0.07087534666061401,
 0.05552757531404495,
 0.019193356856703758,
 -0.02625126577913761,
 -0.01010954286903143,
 -0.026940442621707916,
 0.022307462990283966,
 -0.02222665585577488,
 -0.14969263970851898,
 -0.017493024468421936,
 0.007676282897591591,
 0.054352231323719025,
 0.0032544038258492947,
 0.03172588348388672,
 -0.08462139964103699,
 -0.029405992478132248,
 0.051595550030469894,
 0.048124078661203384,
 -0.003314835485070944,
 -0.05827915295958519,
 0.04196925833821297,
 0.022210702300071716,
 0.1281888633966446,
 -0.022338951006531715,
 -0.011656239628791809,
 0.06292837113142014,
 -0.03287634998559952,
 -0.09122604131698608,
 -0.03117534890770912,
 0.052699536085128784,
 0.04703483358025551,
 -0.08420310169458389,
 -0.030056182295084,
 -0.0207448396

In [17]:
print( "Vector length:", len(vector))

Vector length: 384


In [18]:
from dotenv import load_dotenv
import os
load_dotenv()

True

In [19]:
PINECONE_API_KEY = os.getenv("PINECONE_API_KEY")
GEMINI_API_KEY = os.getenv("GEMINI_API_KEY")

# Ensure the environment variables are present before assigning them to os.environ
if PINECONE_API_KEY is None:
    raise EnvironmentError("PINECONE_API_KEY not set. Please add it to your .env or environment.")
if GEMINI_API_KEY is None:
    raise EnvironmentError("GEMINI_API_KEY not set. Please add it to your .env or environment.")

os.environ["PINECONE_API_KEY"] = PINECONE_API_KEY
os.environ["GEMINI_API_KEY"] = GEMINI_API_KEY

In [20]:
from pinecone import Pinecone 
pinecone_api_key = PINECONE_API_KEY

pc = Pinecone(api_key=pinecone_api_key)

In [21]:
pc

In [22]:
from pinecone import ServerlessSpec 

index_name = "genmedassist"

if not pc.has_index(index_name):
    pc.create_index(
        name = index_name,
        dimension=384,  # Dimension of the embeddings
        metric= "cosine",  # Cosine similarity
        spec=ServerlessSpec(cloud="aws", region="us-east-1")
    )


index = pc.Index(index_name)

In [23]:
from langchain_pinecone import PineconeVectorStore

# Embed each chunk and upsert into Pinecone
docsearch = PineconeVectorStore.from_existing_index(
    index_name=index_name,
    embedding=embedding
)

In [29]:
from langchain_pinecone import PineconeVectorStore

docsearch = PineconeVectorStore.from_documents(
    documents=texts_chunk,
    embedding=embedding,
    index_name=index_name
)

In [30]:
# Load Existing index 

from langchain_pinecone import PineconeVectorStore
# Embed each chunk and upsert the embeddings into your Pinecone index.
docsearch = PineconeVectorStore.from_existing_index(
    index_name=index_name,
    embedding=embedding
)

In [31]:
retriever = docsearch.as_retriever(search_type="similarity", search_kwargs={"k":3})

In [36]:
retrieved_docs = retriever.invoke("What are the benefits of healthy eating  ?")
retrieved_docs

[Document(id='3e4f0998-ca79-4e0c-9a6d-e0160fc3b161', metadata={'source': 'data\\Medical_book.pdf'}, page_content='Prevention Preventive health practices such as healthy diet, daily exercise , stress management, and control of lifestyle habits such as smoking and drinking, can lengthen the life span and improve the quality of life as people age. Exercise can improve the appetite, the health of the bones, the emotional and mental outlook, and the digestion and circulation. Drinking plenty of fluids aids in maintaining healthy skin, good digestion, and proper elimination of wastes. Up to eight glasses of water'),
 Document(id='73abd7a1-5aba-4dfa-bad6-88495bbbf1c8', metadata={'source': 'data\\Medical_book.pdf'}, page_content='Prevention A healthy lifestyle—eating right, regular exercise, maintaining a healthy weight, not smoking, and control- ling hypertension—can reduce the risk of developing atherosclerosis, help keep the disease from progressing, and sometimes cause it to regress. • Eat

In [35]:
retrieved_docs = retriever.invoke("What is acne ?")
retrieved_docs

[Document(id='fd7f84d4-bb0d-4f04-b09a-ec8dfbd8286f', metadata={'source': 'data\\Medical_book.pdf'}, page_content='see Heartburn Acidosis see Respiratory acidosis; Renal tubular acidosis; Metabolic acidosis Acne Definition Acne is a common skin disease characterized by pimples on the face, chest, and back. It occurs when the pores of the skin become clogged with oil, dead skin cells, and bacteria. Description Acne vulgaris, the medical term for common acne, is the most common skin disease. It affects nearly 17 million people in the United States. While acne can arise at any age, it usually begins at puberty'),
 Document(id='cccab26a-d90c-4f03-ae86-3de83a45e9f0', metadata={'source': 'data\\Medical_book.pdf'}, page_content='only for very severe, disfiguring acne. Acne is a skin condition that occurs when pores or hair follicles become blocked. This allows a waxy material, sebum, to collect inside the pores or follicles. Normally, sebum flows out onto the skin and hair to form a protective

In [34]:
ques = retriever.invoke("what are white blood cells ?")
ques

[Document(id='01a8c9b0-0981-4942-a94d-9ec211d29931', metadata={'source': 'data\\Medical_book.pdf'}, page_content='sample. Fewer in number than the red cells, WBCs are the body’s primary means of fighting infection. There are five main types of white cells (neutrophils, lymphocytes, monocytes, eosinophils, and basophils), each of which plays a different role in responding to the presence of foreign organisms in the body. A differential white cell count is done by staining a smear of the patient’s blood with a Wright’s stain, allowing the different types of white cells to be clearly seen under the microscope.'),
 Document(id='a3521ed1-494c-493c-b6f8-3246aceb622b', metadata={'source': 'data\\Medical_book.pdf'}, page_content='white blood cells for both men and women is approximately 4,000–10,000 WBCs per microliter of blood. Abnormal results Abnormal blood count results are seen in a variety of conditions. One of the most common is anemias, which are characterized by low RBC counts, hemogl

In [ ]:
ques = retriever.invoke("what is acid phosphatase test?")
ques

In [33]:
ques = retriever.invoke("diagnosis of diabetes?")
ques

[Document(id='104b2328-ed36-425c-9556-268c7220b1b8', metadata={'source': 'data\\Medical_book.pdf'}, page_content='of Laboratory and Diagnostic Tests.5th ed. Ed. Francis Fishback. Philadelphia: Lippincott, 1996. Henry, John B., ed. Clinical Diagnosis and Management by Laboratory Methods. 19th ed. Philadelphia: W. B. Saun- ders Co., 1996. PERIODICALS American Diabetes Association. “Report of the Expert Com- mittee on the Diagnosis and Classification of Diabetes Mellitus.” Diabetes Care 20, no, 7(July 997): 1183-1197. ORGANIZATIONS American Diabetes Association. 1701 North Beauregard Street, Alexandria, V A'),
 Document(id='4fb7984a-0134-4645-9df7-3cff39d80e9f', metadata={'source': 'data\\Medical_book.pdf'}, page_content='begin to fall. A person with diabetes mellitus either does not make enough insulin, or makes insulin that does not work properly. The result is blood sugar that remains high, a condition called hyperglycemia. Diabetes must be diagnosed as early as possible. If left untre